
<img src="https://github.com/QuentinAmbard/databricks-demo/raw/main/retail/resources/images/delta-lake-perf-bench.png" width="500" style="float: right; margin-left: 50px"/>

# Delta Lake: Performance made simple

## Blazing fast query at scale

Delta Lake saves all your table metadata in an efficient format, ranging from efficient queries on small tables (GB) to massive PB-scale tables. 

Delta Lake is designed to be smart and do all the hard job for you. It'll automatically tune your table and read the minimum data required to be able to satisfied your query.

This result in **fast read query**, even with a growing number of data/partitions!


In this notebook, we'll see how we can leverage Delta Lake unique capabilities to speedup requests and simplify maintenance operation. For more details, we recommend to read the [documentation](https://docs.databricks.com/delta/file-mgmt.html).

<!-- Collect usage data (view). Remove it to disable collection. View README for more details.  -->
<img width="1px" src="https://ppxrzfxige.execute-api.us-west-2.amazonaws.com/v1/analytics?category=data-engineering&org_id=7474644512555519&notebook=%2F02-Delta-Lake-Performance&demo_name=delta-lake&event=VIEW&path=%2F_dbdemos%2Fdata-engineering%2Fdelta-lake%2F02-Delta-Lake-Performance&version=1">
<!-- [metadata={"description":"Quick introduction to Delta Lake. <br/><i>Use this content for quick Delta demo.</i>",
 "authors":["quentin.ambard@databricks.com"],
 "db_resources":{}}] -->

In [0]:
%run ./_resources/00-setup $reset_all_data=false

## Configuration file

Please change your catalog and schema here to run the demo on a different catalog.

<!-- Collect usage data (view). Remove it to disable collection or disable tracker during installation. View README for more details.  -->
<img width="1px" src="https://ppxrzfxige.execute-api.us-west-2.amazonaws.com/v1/analytics?category=data-engineering&org_id=7474644512555519&notebook=%2Fconfig&demo_name=delta-lake&event=VIEW&path=%2F_dbdemos%2Fdata-engineering%2Fdelta-lake%2Fconfig&version=1">


# Technical Setup notebook. Hide this cell results
Initialize dataset to the current user and cleanup data when reset_all_data is set to true

Do not edit

USE CATALOG `main`
using catalog.database `main`.`dbdemos_delta_lake`


##![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Delta Lake Liquid Clustering

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/delta/delta-liquid-1.png?raw=true" style="float: right" width="450px">

Data Layout is key to increase performance and query speed. Manual tuning trough hive-style partitioning is not efficient (creating too big or small partitions) and hard to maintain.

To solve this issue, Delta Lake released Liquid Clustering. Liquid will automatically adjusts the data layout based on clustering keys, which helps to avoid the over or under-partitioning problems that can occur with Hive partitioning.

Liquid clustering can be specified on any columns to provide fast access, including high cardinality or data skew. 

* **Liquid is simple**: You set Liquid clustering keys on the columns that are most often queried - no more worrying about traditional considerations like column cardinality, partition ordering, or creating artificial columns that act as perfect partitioning keys.
* **Liquid is efficient**: It incrementally clusters new data, so you don't need to trade off between improving performance with reducing cost/write amplification.
* **Liquid is flexible**: You can quickly change which columns are clustered by Liquid without rewriting existing data.

**Delta Liquid Clustering requires DBR 13.2**

For more details, [please read the documentation](https://docs.databricks.com/delta/clustering.html)

In [0]:
-- Liquid will properly layout the data to speedup queries by firstname or lastname.
-- this is done by adding the CLUSTER BY keyword during your standard table creation. Clustered table can't have partitions.
CREATE OR REPLACE TABLE user_clustering CLUSTER BY (firstname, lastname)
  AS SELECT * FROM user_delta;

num_affected_rows num_inserted_rows

In [0]:
select * from user_clustering;

id creation_date firstname lastname email address gender age_group 457 2026-02-07T18:24:52.000Z Kelly Carter qpreston@diaz.net 25890 Hines Forges
North Isabella, NH 21484 1 2 288 2026-02-08T15:36:57.000Z Mark Murphy ohowell@walters.net 532 Jerry Alley
Ginaland, PW 79970 0 4 1005 2026-02-20T22:36:46.000Z Michaela Hodge smithjohn@waters.com 863 Arthur Ports
Port Michaelshire, AZ 76935 1 1 1159 2026-02-19T11:36:09.000Z Laura Pope ericahaas@pope-riggs.com USCGC Young
FPO AE 65179 0 5 548 2026-02-04T12:19:41.000Z Edward Hernandez elang@barnes.info 451 Valenzuela Trace Suite 441
New Peggy, AR 59692 1 2 374 2026-02-07T22:19:37.000Z Kenneth Evans vazquezroger@hernandez.net 33521 Kathryn Points
East Christian, NJ 76300 0 1 510 2026-02-03T17:34:06.000Z David Wilson danielle17@powell.com 5039 Jesse Extensions Apt. 367
Bellview, NC 83060 1 5 162 2026-02-13T15:45:49.000Z Amy Stephens kristi80@howard.com 295 Richards Ports
Wrightberg, VI 69783 1 2 972 2026-02-11T14:15:10.000Z Stephen Bryant allenjason@meyer-johnson.com PSC 1416, Box 4658
APO AE 12698 1 3 1162 2026-02-12T21:12:23.000Z William Dixon roger09@lee-stark.com 44234 Mason Union Suite 083
East Jessica, MT 26721 0 10 163 2026-02-20T10:48:06.000Z Mary Copeland kimberlyhernandez@wilson.com 50150 Christian Stravenue
West Hayley, KS 99339 1 2 160 2026-02-19T22:58:30.000Z Lisa Ochoa joy86@jimenez.com 1856 Hicks Bypass Suite 948
East Jeffrey, AS 23509 0 4 1104 2026-02-01T02:01:35.000Z Adam Smith mark26@wolf.org 71664 Shaun Squares
West Bryan, IL 34770 1 9 367 2026-02-11T14:52:44.000Z Stephen Bryant richardbarton@crawford-hughes.info 93134 Wells Greens Apt. 517
West Peterville, WI 52494 1 1 1224 2026-02-21T09:33:59.000Z Natalie Rich hannadaniel@sanchez.com 92797 Smith Rue
New Brittany, CO 58647 1 6 577 2026-02-12T02:43:57.000Z Timothy Mendoza kylelam@taylor.com 5219 Natasha Pines Suite 238
North Karenburgh, RI 65013 1 7 1111 2026-02-05T02:54:05.000Z Gregory Thompson tbailey@mccullough.com 017 Katelyn Falls
South Tamaraside, ME 11330 1 3 887 2026-02-20T18:35:45.000Z Melissa Jefferson donaldtucker@lopez.org 646 Kevin Gardens Suite 449
Edwinbury, PR 33673 0 3 93 2026-02-12T00:30:14.000Z Thomas Wells michaelstanley@davis.com 84838 Cynthia Meadow Suite 118
Jamesside, FL 00584 1 9 218 2026-02-19T12:51:24.000Z Laura Salinas hardingtammy@harris.org 823 Sherry Springs Suite 805
Danamouth, AR 02938 0 4 563 2026-02-01T04:38:34.000Z Alan Smith johnsontony@allen-thompson.com 44777 Danielle Fords Apt. 479
Matthewside, FL 17119 0 6 416 2026-02-17T05:25:53.000Z Helen Wolfe melissa40@salazar-lane.net PSC 1350, Box 0351
APO AP 41334 1 4 1028 2026-02-04T04:26:49.000Z Derrick Taylor agarcia@mitchell.com 1820 Katrina Cliffs Suite 065
New Michaelhaven, NH 32888 1 6 815 2026-02-03T09:49:58.000Z Dale Garcia uparker@king.com 42217 Rivas Brooks
Williamview, WA 11924 0 6 1205 2026-02-07T18:57:18.000Z Kelly Carter erios@martin.com 11879 Stevens Skyway
New Marcus, UT 23886 1 9 1086 2026-02-19T03:04:31.000Z Kimberly Chan harteric@nash-clark.org 56917 Kathryn Canyon Apt. 211
Lake Brianchester, WY 09619 1 3 536 2026-02-02T02:22:52.000Z Brandon Williams lauren99@bell.com 5870 Ramos Plains Suite 111
Meyerchester, NJ 60452 1 8 32 2026-02-03T17:45:01.000Z David Wilson matthew89@williamson.com 8360 Ashley Radial Suite 392
Lake Jacob, IA 33234 1 1 743 2026-02-16T20:05:56.000Z Erin Maldonado sydney94@stewart-little.biz 867 Ana Greens Apt. 238
North Timothyview, AS 59613 1 4 1004 2026-02-12T21:02:20.000Z William Dixon marywashington@martin-montes.com 00772 Jones Via
New Justinmouth, OK 12772 1 1 988 2026-02-08T06:23:48.000Z Larry Edwards reyesmelissa@powell.com 14520 Patricia Springs
West Danaburgh, FL 08638 1 10 827 2026-02-09T10:46:29.000Z Michael Cox juliecross@scott.biz 386 Suzanne Village Apt. 259
North Sarahfort, NH 28334 1 5 941 2026-02-12T06:14:22.000Z Todd Washington wolfelevi@green-vasquez.com 790 Owens Pike
Patrickborough, ME 66480 0 6 165 2026-02-07T12:24:15.000Z Juan Ramirez dustinbailey@ray.com 57009 Shepherd Cove
J

In [0]:
SELECT * FROM user_delta;

id creation_date firstname lastname email address gender age_group 457 2026-02-07T18:24:52.000Z Kelly Carter qpreston@diaz.net 25890 Hines Forges
North Isabella, NH 21484 1 2 288 2026-02-08T15:36:57.000Z Mark Murphy ohowell@walters.net 532 Jerry Alley
Ginaland, PW 79970 0 4 1005 2026-02-20T22:36:46.000Z Michaela Hodge smithjohn@waters.com 863 Arthur Ports
Port Michaelshire, AZ 76935 1 1 1159 2026-02-19T11:36:09.000Z Laura Pope ericahaas@pope-riggs.com USCGC Young
FPO AE 65179 0 5 548 2026-02-04T12:19:41.000Z Edward Hernandez elang@barnes.info 451 Valenzuela Trace Suite 441
New Peggy, AR 59692 1 2 374 2026-02-07T22:19:37.000Z Kenneth Evans vazquezroger@hernandez.net 33521 Kathryn Points
East Christian, NJ 76300 0 1 510 2026-02-03T17:34:06.000Z David Wilson danielle17@powell.com 5039 Jesse Extensions Apt. 367
Bellview, NC 83060 1 5 162 2026-02-13T15:45:49.000Z Amy Stephens kristi80@howard.com 295 Richards Ports
Wrightberg, VI 69783 1 2 972 2026-02-11T14:15:10.000Z Stephen Bryant allenjason@meyer-johnson.com PSC 1416, Box 4658
APO AE 12698 1 3 1162 2026-02-12T21:12:23.000Z William Dixon roger09@lee-stark.com 44234 Mason Union Suite 083
East Jessica, MT 26721 0 10 163 2026-02-20T10:48:06.000Z Mary Copeland kimberlyhernandez@wilson.com 50150 Christian Stravenue
West Hayley, KS 99339 1 2 160 2026-02-19T22:58:30.000Z Lisa Ochoa joy86@jimenez.com 1856 Hicks Bypass Suite 948
East Jeffrey, AS 23509 0 4 1104 2026-02-01T02:01:35.000Z Adam Smith mark26@wolf.org 71664 Shaun Squares
West Bryan, IL 34770 1 9 367 2026-02-11T14:52:44.000Z Stephen Bryant richardbarton@crawford-hughes.info 93134 Wells Greens Apt. 517
West Peterville, WI 52494 1 1 1224 2026-02-21T09:33:59.000Z Natalie Rich hannadaniel@sanchez.com 92797 Smith Rue
New Brittany, CO 58647 1 6 577 2026-02-12T02:43:57.000Z Timothy Mendoza kylelam@taylor.com 5219 Natasha Pines Suite 238
North Karenburgh, RI 65013 1 7 1111 2026-02-05T02:54:05.000Z Gregory Thompson tbailey@mccullough.com 017 Katelyn Falls
South Tamaraside, ME 11330 1 3 887 2026-02-20T18:35:45.000Z Melissa Jefferson donaldtucker@lopez.org 646 Kevin Gardens Suite 449
Edwinbury, PR 33673 0 3 93 2026-02-12T00:30:14.000Z Thomas Wells michaelstanley@davis.com 84838 Cynthia Meadow Suite 118
Jamesside, FL 00584 1 9 218 2026-02-19T12:51:24.000Z Laura Salinas hardingtammy@harris.org 823 Sherry Springs Suite 805
Danamouth, AR 02938 0 4 563 2026-02-01T04:38:34.000Z Alan Smith johnsontony@allen-thompson.com 44777 Danielle Fords Apt. 479
Matthewside, FL 17119 0 6 416 2026-02-17T05:25:53.000Z Helen Wolfe melissa40@salazar-lane.net PSC 1350, Box 0351
APO AP 41334 1 4 1028 2026-02-04T04:26:49.000Z Derrick Taylor agarcia@mitchell.com 1820 Katrina Cliffs Suite 065
New Michaelhaven, NH 32888 1 6 815 2026-02-03T09:49:58.000Z Dale Garcia uparker@king.com 42217 Rivas Brooks
Williamview, WA 11924 0 6 1205 2026-02-07T18:57:18.000Z Kelly Carter erios@martin.com 11879 Stevens Skyway
New Marcus, UT 23886 1 9 1086 2026-02-19T03:04:31.000Z Kimberly Chan harteric@nash-clark.org 56917 Kathryn Canyon Apt. 211
Lake Brianchester, WY 09619 1 3 536 2026-02-02T02:22:52.000Z Brandon Williams lauren99@bell.com 5870 Ramos Plains Suite 111
Meyerchester, NJ 60452 1 8 32 2026-02-03T17:45:01.000Z David Wilson matthew89@williamson.com 8360 Ashley Radial Suite 392
Lake Jacob, IA 33234 1 1 743 2026-02-16T20:05:56.000Z Erin Maldonado sydney94@stewart-little.biz 867 Ana Greens Apt. 238
North Timothyview, AS 59613 1 4 1004 2026-02-12T21:02:20.000Z William Dixon marywashington@martin-montes.com 00772 Jones Via
New Justinmouth, OK 12772 1 1 988 2026-02-08T06:23:48.000Z Larry Edwards reyesmelissa@powell.com 14520 Patricia Springs
West Danaburgh, FL 08638 1 10 827 2026-02-09T10:46:29.000Z Michael Cox juliecross@scott.biz 386 Suzanne Village Apt. 259
North Sarahfort, NH 28334 1 5 941 2026-02-12T06:14:22.000Z Todd Washington wolfelevi@green-vasquez.com 790 Owens Pike
Patrickborough, ME 66480 0 6 165 2026-02-07T12:24:15.000Z Juan Ramirez dustinbailey@ray.com 57009 Shepherd Cove
J

In [0]:
-- review the table definition, Liquid Clustering appears under "Clustering Information"
DESCRIBE TABLE user_clustering;

col_name data_type comment id bigint null creation_date timestamp null firstname string null lastname string null email string null address string null gender int null age_group int null # Clustering Information # col_name data_type comment firstname string null lastname string null


### How to trigger liquid clustering
<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/delta/delta-liquid-2.png?raw=true" style="float: right" width="400px">


Liquid clustering is incremental, meaning that data is only rewritten as necessary to accommodate data that needs to be clustered.

For best performance, Databricks recommends scheduling regular OPTIMIZE jobs to cluster data. 

For tables experiencing many updates or inserts, Databricks recommends scheduling an OPTIMIZE job every one or two hours. 

Because liquid clustering is incremental, most OPTIMIZE jobs for clustered tables run quickly. No need to specify any ZORDER columns.

*Note: Liquid clustering will automatically re-arrange your data during writes above a given threshold. As with all indexes, this will add a small write cost.*

In [0]:
OPTIMIZE user_clustering;

path metrics List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 0, null, null, 0, 0, 1, 0, false, 0, 0, 1771916864266, 1771916869121, 8, 0, null, List(0, 0), null, 8, 8, 0, 0, List(147524, true, false, false, null, null, null, null, 0, 0, 0, 0, 1, 147524, 147524, null, log, 16777216, 67108864, 4, 0, 0, null, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, List(128, 78, 0, 0, 0, 1968), 2, 1, 5, sizeAware, false, 0, null), null) List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 0, null, null, 0, 0, 1, 1, true, 0, 0, 1771916869180, 1771916871198, 8, 0, null, List(0, 0), null, 8, 8, 0, 0, List(147524, false, false, false, null, null, null, post-optimize-compaction, 0, 0, 0, 0, 0, 0, 0, null, null, 33554432, 67108864, 0, 0, 0, null, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, List(0, 0, 927, 0, 0, 0), 15, 1, 1, null, false, 0, null), null)

In [0]:
VACUUM user_clustering;

path

In [0]:
SELECT * FROM user_clustering where firstname = 'Teresa'

id creation_date firstname lastname email address gender age_group 25769804295 2026-02-23T14:37:28.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 1 8 25769804453 2026-02-23T14:00:20.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 1 5 407 2026-02-23T14:18:14.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 1 3 8589934999 2026-02-23T14:18:14.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 0 10 42949673479 2026-02-23T14:37:28.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 0 1 42949673367 2026-02-23T14:18:13.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 1 4 60129542551 2026-02-23T14:18:14.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 1 7 8589935269 2026-02-23T14:00:20.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 0 6 17179869861 2026-02-23T14:00:20.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 1 0 519 2026-02-23T14:37:29.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 1 1 8589935111 2026-02-23T14:37:29.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 1 9 17179869703 2026-02-23T14:37:29.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 1 10 25769804183 2026-02-23T14:18:13.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 0 6 51539607959 2026-02-23T14:18:13.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 1 5 51539608229 2026-02-23T14:00:19.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 1 6 677 2026-02-23T14:00:20.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 1 3 17179869591 2026-02-23T14:18:14.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 1 0 34359739045 2026-02-23T14:00:20.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 1 9 34359738775 2026-02-23T14:18:14.000Z Teresa Stanton philiprodriguez@perez.com Unit 1017 Box 8110
DPO AE 87315 0 5 34359738887 2026-02-23T14:37:29.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 0 6 42949673637 2026-02-23T14:00:20.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 0 9 51539608071 2026-02-23T14:37:28.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 1 2 60129542663 2026-02-23T14:37:29.000Z Teresa Kaufman mitchellterri@mccall-tucker.net 5458 Alan Plains Suite 081
Lake Paul, NC 22327 1 5 60129542821 2026-02-23T14:00:20.000Z Teresa Mata sbrewer@campbell-baker.biz 8644 Rachael Green
Wardshire, MO 54602 1 2

### Dynamically changing your clustering columns

Liquid table are flexible, you can change your clustering columns without having to re-write all your data. 

Let's make sure our table provides fast queries for ID:

In [0]:
ALTER TABLE user_clustering CLUSTER BY (id, firstname, lastname);

In [0]:
-- Disable liquid clustering:
ALTER TABLE user_clustering CLUSTER BY NONE;
-- Note: this does not rewrite data that has already been clustered, but prevents future OPTIMIZE operations from using clustering keys.

### Cluster by Auto

In Databricks Runtime 15.4 LTS and above, you can enable automatic liquid clustering for Unity Catalog managed Delta tables. With automatic liquid clustering enabled, Databricks intelligently chooses clustering keys to optimize query performance. You enable automatic liquid clustering using the CLUSTER BY AUTO clause.

When enabled, automatic key selection and clustering operations run asynchronously as a maintenance operation and require that predictive optimization is enabled for the table.

In [0]:
ALTER TABLE user_clustering CLUSTER BY AUTO;

In [0]:
DESCRIBE EXTENDED user_clustering

--Predictive Optimization	ENABLE (inherited from METASTORE unity-catalog-demo)

col_name data_type comment id bigint null creation_date timestamp null firstname string null lastname string null email string null address string null gender int null age_group int null # Clustering Information # col_name data_type comment # Delta Statistics Columns Column Names email, firstname, age_group, id, address, gender, creation_date, lastname Column Selection Method first-32 # Detailed Table Information Catalog main Database dbdemos_delta_lake Table user_clustering Created Time Tue Feb 24 07:02:40 UTC 2026 Last Access UNKNOWN Created By Spark Type MANAGED Location Provider delta Owner rishavkumar7011@gmail.com Is_managed_location true Predictive Optimization ENABLE (inherited from METASTORE metastore_aws_us_east_2) Table Properties [clusterByAuto=true,clusteringColumns=[],delta.checkpointPolicy=v2,delta.enableDeletionVectors=true,delta.enableRowTracking=true,delta.feature.appendOnly=supported,delta.feature.clustering=supported,delta.feature.deletionVectors=supported,delta.feature.domainMetadata=supported,delta.feature.invariants=supported,delta.feature.rowTracking=supported,delta.feature.v2Checkpoint=supported,delta.minReaderVersion=3,delta.minWriterVersion=7,delta.parquet.compression.codec=zstd,delta.rowTracking.materializedRowCommitVersionColumnName=_row-commit-version-col-322a2504-3f0e-4d9b-a99c-8cf0cfde1913,delta.rowTracking.materializedRowIdColumnName=_row-id-col-fbdc3ba5-a15c-4565-a0c9-bc8c3f397f16]

In [0]:
OPTIMIZE user_clustering;

path metrics List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 0, null, null, 0, 0, 1, 1, true, 0, 0, 1771917358350, 1771917358854, 8, 0, null, List(0, 0), null, 8, 8, 0, 0, null, null)

In [0]:
VACUUM user_clustering;

path

### Auto Liquid Clustering will dynamically change the cluster keys based on the read/write pattern on the table based on column filters, merge keys etc

###![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Compacting without Liquid Clustering

While recommended to accelerate your queries, some tables might not always have Liquid Clustering enabled.

Adding data to the table results in new file creation, and your table can quickly have way too many small files which is going to impact performances over time.

This becomes expecially true with streaming operation where you add new data every few seconds, in near realtime.

Just like for Liquid Clusteing, Delta Lake solves this operation with the `OPTIMIZE` command, which is going to optimize the file layout for you, picking the proper file size based on heuristics. As no Cluster are defined, this will simply compact the files.

In [0]:
-- let's compact our table. Note that the engine decided to compact 8 files into 1 ("numFilesAdded": 1, "numFilesRemoved": 8)
OPTIMIZE user_delta 

path metrics List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 0, null, null, 0, 0, 1, 1, true, 0, 0, 1771917525448, 1771917526077, 8, 0, null, List(0, 0), null, 8, 8, 0, 0, null, null)

These maintenance operation have to be triggered frequently to keep our table properly optimized.

Using Databricks, you can have your table automatically optimized out of the box, without having you to worry about it. All you have to do is set the [proper table properties](https://docs.databricks.com/optimizations/auto-optimize.html), and the engine will optimize your table when needed, without having you to run manual OPTIMIZE operation.

We strongly recommend to enable this option for all your tables.

In [0]:
ALTER TABLE user_delta SET TBLPROPERTIES (delta.autoOptimize.optimizeWrite = true, delta.autoOptimize.autoCompact = true);

### Note: Auto Optimize with Liquid Clustering

Liquid Clustering will automatically kick off eager optimization starting from a given write size, based on heuristic. 
You can also turn on `delta.autoOptimize.optimizeWrite = true` on your liquid table starting from DBR 13.3 to make sure all writes will be optimized. While you can enable `delta.autoOptimize.autoCompact = true`, it won't have any effect for now (as of DBR 13.3, this might change in the future).

## Legacy file layout optimizations

Liquid Clustering is the future of Delta Lake optimization and query speedup, and we now recommend starting with Liquid Clustering.

Below are previous Delta Lake optimization leveraging Zordering and Partitioning techniques. 

### ZORDER


ZORDER will optimize the file layout by multiple columns, but it's often used in addition to partitioning and is not as efficient as Liquid Clustering. It'll increase the write amplification and won't solve your small partitions issues.

Below are a few examples on how you can leverage ZORDER, but we strongly recommend switching to Liquid Tables instead.

### ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Adding indexes (ZORDER) to your table

If you request your table using a specific predicat (ex: username), you can speedup your request by adding an index on these columns. We call this operation ZORDER.

You can ZORDER on any column, especially the one having high cardinality (id, firstname etc). 

*Note: We recommand to stay below 4 ZORDER columns for better query performance.*

In [0]:
OPTIMIZE user_delta ZORDER BY (id, firstname);

-- our next queries using a filter on id or firstname will be much faster
SELECT * FROM user_delta where id = 4 or firstname = 'Quentin';

id creation_date firstname lastname email address gender age_group 4 2026-02-24T05:46:54.000Z Yvonne Cooke baileyjulie@burgess-wagner.biz 636 Regina Divide
Dawsonport, MN 67880 1 0

### ![Delta Lake Tiny Logo](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Delta Lake Generated columns for dynamic partitions

Adding partitions to your table is a way of saving data having the same column under the same location. Our engine will then be able to read less data and have better read performances.

Using Delta Lake, partitions can be generated based on expression, and the engine will push-down your predicate applying the same expression even if the request is on the original field.

A typical use-case is to partition per a given time (ex: year, month or even day). 

Our user table has a `creation_date` field. We'll generate a `creation_day` field based on an expression and use it as partition for our table with `GENERATED ALWAYS`.

In addition, we'll let the engine generate incremental ID.

*Note: Remember that partition will also create more files under the hood. You have to be careful using them. Make sure you don't over-partition your table (aim for 100's of partition max, having at least 1GB of data). We don't recommend creating partition on table smaller than 1TB. Use LIQUID CLUSTERING instead.*

In [0]:
CREATE TABLE IF NOT EXISTS user_delta_partition (
  id BIGINT GENERATED ALWAYS AS IDENTITY ( START WITH 10000 INCREMENT BY 1 ), 
  firstname STRING, 
  lastname STRING, 
  email STRING, 
  address STRING, 
  gender INT, 
  age_group INT,
  creation_date timestamp, 
  creation_day date GENERATED ALWAYS AS ( CAST(creation_date AS DATE) ) )
PARTITIONED BY (creation_day);

In [0]:
-- Note that we don't insert data for the creation_day field or id. The engine will handle that for us:
INSERT INTO user_delta_partition (firstname, lastname, email, address, gender, age_group, creation_date) SELECT
  firstname,
  lastname,
  email,
  address,
  gender,
  age_group,
  creation_date
FROM user_delta;

num_affected_rows num_inserted_rows 10000 10000

In [0]:
SELECT * FROM user_delta_partition where creation_day = CAST(NOW() as DATE) ;

id firstname lastname email address gender age_group creation_date creation_day 10035 Wendy Barajas steinregina@durham.biz 24071 Salas Radial
New Brianastad, SC 56118 0 0 2026-02-24T04:06:19.000Z 2026-02-24 10038 Victoria Mcknight wendythompson@johnson-adams.org 13713 Cunningham Groves
Harrisport, MA 53820 1 4 2026-02-24T02:30:35.000Z 2026-02-24 10365 Wanda Cooley sarahmatthews@eaton-fitzpatrick.com 252 Carrie Park Apt. 369
East Jamie, ND 90068 0 4 2026-02-24T03:00:11.000Z 2026-02-24 10405 Wanda Cooley barnesshannon@roth.com 88598 Trevor Ports
North Arthur, ME 94102 1 3 2026-02-24T03:03:13.000Z 2026-02-24 10500 Victoria Kaiser wilsonanthony@walls.info 50534 Bradley Corner
East Stephanie, CA 92495 1 5 2026-02-24T02:01:01.000Z 2026-02-24 10671 Wanda Carney morgansnyder@hayes.biz 87359 Cameron Dale
North Cynthia, ND 17254 1 4 2026-02-24T03:15:09.000Z 2026-02-24 10737 Wendy Ferrell daviessteven@carroll.com 60436 Nguyen Trail
Edwardburgh, NE 55292 1 9 2026-02-24T03:41:24.000Z 2026-02-24 10741 Veronica Mooney wthomas@miller-berger.com USCGC Ruiz
FPO AP 33391 0 5 2026-02-24T00:33:08.000Z 2026-02-24 10799 Wanda Cooley barnesshannon@roth.com 88598 Trevor Ports
North Arthur, ME 94102 1 9 2026-02-24T03:03:13.000Z 2026-02-24 10841 Veronica Fritz cooperjohn@olsen-johnson.com 840 Lawson Brook
Butlerberg, MI 11755 0 4 2026-02-24T00:11:13.000Z 2026-02-24 10926 Yvonne Cooke baileyjulie@burgess-wagner.biz 636 Regina Divide
Dawsonport, MN 67880 0 1 2026-02-24T05:46:54.000Z 2026-02-24 10927 Wendy Barajas steinregina@durham.biz 24071 Salas Radial
New Brianastad, SC 56118 1 0 2026-02-24T04:06:18.000Z 2026-02-24 10958 Victoria Haney orrmichelle@mcclure-carter.info 997 Miller Fords
Elijahberg, PR 85068 0 7 2026-02-24T01:58:09.000Z 2026-02-24 11116 Yvonne Cooke baileyjulie@burgess-wagner.biz 636 Regina Divide
Dawsonport, MN 67880 1 9 2026-02-24T05:46:54.000Z 2026-02-24 11134 Veronica Branch amber11@fernandez.com 244 Patricia Skyway Suite 673
New Ronald, DC 34882 1 1 2026-02-24T00:17:54.000Z 2026-02-24 11162 Veronica Fritz cooperjohn@olsen-johnson.com 840 Lawson Brook
Butlerberg, MI 11755 1 6 2026-02-24T00:11:14.000Z 2026-02-24 11164 Wendy Osborn owalton@rodriguez.com 1218 Hughes Radial
West Christineberg, NH 85773 0 3 2026-02-24T04:18:43.000Z 2026-02-24 11218 Wendy Ferrell daviessteven@carroll.com 60436 Nguyen Trail
Edwardburgh, NE 55292 0 2 2026-02-24T03:41:24.000Z 2026-02-24 11267 Wendy Barajas steinregina@durham.biz 24071 Salas Radial
New Brianastad, SC 56118 1 3 2026-02-24T04:06:18.000Z 2026-02-24 11447 Wendy Ferrell daviessteven@carroll.com 60436 Nguyen Trail
Edwardburgh, NE 55292 0 3 2026-02-24T03:41:23.000Z 2026-02-24 11676 Veronica Mooney wthomas@miller-berger.com USCGC Ruiz
FPO AP 33391 1 1 2026-02-24T00:33:07.000Z 2026-02-24 11960 Veronica Mooney wthomas@miller-berger.com USCGC Ruiz
FPO AP 33391 0 3 2026-02-24T00:33:07.000Z 2026-02-24 12042 Victoria Braun christopherbean@martinez-cox.com 994 Howard Turnpike Suite 894
Craigtown, KS 48365 0 7 2026-02-24T01:22:31.000Z 2026-02-24 12137 Victoria Haney orrmichelle@mcclure-carter.info 997 Miller Fords
Elijahberg, PR 85068 1 1 2026-02-24T01:58:09.000Z 2026-02-24 12168 Wanda Cooley sarahmatthews@eaton-fitzpatrick.com 252 Carrie Park Apt. 369
East Jamie, ND 90068 1 4 2026-02-24T03:00:10.000Z 2026-02-24 12177 Yvonne Cooke baileyjulie@burgess-wagner.biz 636 Regina Divide
Dawsonport, MN 67880 1 0 2026-02-24T05:46:54.000Z 2026-02-24 12207 Wendy Ferrell daviessteven@carroll.com 60436 Nguyen Trail
Edwardburgh, NE 55292 1 1 2026-02-24T03:41:23.000Z 2026-02-24 12328 Victoria Mcknight wendythompson@johnson-adams.org 13713 Cunningham Groves
Harrisport, MA 53820 1 4 2026-02-24T02:30:35.000Z 2026-02-24 12395 Veronica Branch amber11@fernandez.com 244 Patricia Skyway Suite 673
New Ronald, DC 34882 1 1 2026-02-24T00:17:54.000Z 2026-02-24 12429 Veronica Mooney wthomas@miller-berger.com USCGC Ruiz
FPO AP 33391 1 10 2026-02-24T00:33:08.000Z 2026-02-24 12454 Veronica Fritz cooperjohn@olsen-johnson.com 840 Lawson Brook
B

That's it! You know how to have super fast queries on top of your Delta Lake tables!


Next: Discover how Delta Lake is an Universal Format with [the 03-Delta-Lake-Uniform notebook]($./03-Delta-Lake-Uniform) or go back to [00-Delta-Lake-Introduction]($./00-Delta-Lake-Introduction).
